In [ ]:
pip install noisereduce

In [ ]:
import moviepy.editor as mp
import noisereduce as nr
import sys
import os
import numpy as np
import IPython
from scipy.io import wavfile
# to use this notebook with colab uncomment the next line
!git clone https://github.com/MTG/sms-tools.git
# and change the next line to sys.path.append('sms-tools/software/models/')
sys.path.append('sms-tools/software/models/')
from utilFunctions import wavread, wavwrite

Imageio: 'ffmpeg-linux64-v3.3.1' was not found on your computer; downloading it now.
Try 1. Download from https://github.com/imageio/imageio-binaries/raw/master/ffmpeg/ffmpeg-linux64-v3.3.1 (43.8 MB)
Downloading: 8192/45929032 bytes (0.0%)2891776/45929032 bytes (6.3%)6627328/45929032 bytes (14.4%)10280960/45929032 bytes (22.4%)14041088/45929032 bytes (30.6%)17727488/45929032 bytes (38.6%)21356544/45929032 bytes (46.5%)25001984/45929032 bytes (54.4%)28729344/45929032 bytes (62.6%)32382976/45929032 bytes (70.5%)36151296/45929032 bytes (78.7%)39813120/45929032 bytes (86.7%)43491328/45929032 bytes (94.7%)

In [ ]:
def stereoToMono(audiodata):
    newaudiodata = []

    for i in range(len(audiodata)):
        d = (audiodata[i][0] + audiodata[i][1])/2
        newaudiodata.append(d)

    return np.array(newaudiodata, dtype='int16')

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


# REMOVE BACKGROUND NOISE OF ALL THE VIDEOS


In [ ]:
#name of the files
file = ['bi1-e01','bi1-e03','bi1-e04','bi1-e05','bi1-e06','bi1-e07','bi1-e08','bi1-e09','bi1-e11','bi1-e12','bi1-e13','bi1-e14','bi1-e15','bi1-e16','bi1-e17','bi1-e18','bi1-e19','bi1-e20','bi1-e22','bi1-e23','bi1-e24','bi1-e26','bi1-e28','bi1-e31','bi1-e32','bi1-e34','bi1-e36','bi1-e37','bi1-f01','bi1-f02','bi1-f03','bi1-f04','bi1-f05','bi1-f06','bi1-f07','bi1-f08','bi1-f09','bi1-f11','bi1-f12','bi1-f13','bi1-f14','bi1-f15','bi1-f16','bi1-f17','bi1-f18','bi1-f19','bi1-f20','bi1-f21','bi1-f23','bi1-f26','bi1-f27','bi1-f28','bi1-f29','bi1-f31','bi1-f32','bi1-f34','bi1-f36','bi1-f37','bi2-e01','bi2-e02','bi2-e03','bi2-e04','bi2-e05','bi2-e06','bi2-e07','bi2-e08','bi2-e09','bi2-e11','bi2-e12','bi2-e13','bi2-e14','bi2-e15','bi2-e16','bi2-e17','bi2-e19','bi2-e20','bi2-e21','bi2-e22','bi2-e23','bi2-e26','bi2-e28','bi2-e31','bi2-e32','bi2-e34','bi2-e36','bi2-e37','bi2-f01','bi2-f03','bi2-f04','bi2-f05','bi2-f06','bi2-f07','bi2-f08','bi2-f09','bi2-f10','bi2-f11','bi2-f12','bi2-f13','bi2-f14','bi2-f15','bi2-f16','bi2-f17','bi2-f19','bi2-f20','bi2-f23','bi2-f26','bi2-f27','bi2-f28','bi2-f29','bi2-f31','bi2-f32','bi2-f34','bi2-f36','bi2-f37','bi6-e01','bi6-e03','bi6-e04','bi6-e05','bi6-e06','bi6-e07','bi6-e08','bi6-e09','bi6-e11','bi6-e12','bi6-e13','bi6-e14','bi6-e15','bi6-e16','bi6-e17','bi6-e18','bi6-e19','bi6-e20','bi6-e21','bi6-e23','bi6-e26','bi6-e28','bi6-e31','bi6-e32','bi6-e33','bi6-e34','bi6-e36','bi6-e37','bi6-f01','bi6-f02','bi6-f03','bi6-f04','bi6-f05','bi6-f06','bi6-f07','bi6-f08','bi6-f09','bi6-f11','bi6-f12','bi6-f13','bi6-f14','bi6-f15','bi6-f16','bi6-f17','bi6-f18','bi6-f19','bi6-f20','bi6-f22','bi6-f23','bi6-f26','bi6-f28','bi6-f31','bi6-f32','bi6-f34','bi6-f36','bi6-f37']
print(len(file))

170


In [ ]:
for clip in range(len(file)):
  
  #extract the audio from the video
  my_clip = mp.VideoFileClip(r'/content/drive/MyDrive/WhitneyWeikum_AVSpeech/'+file[clip]+'.avi')
  my_clip.audio.write_audiofile(r'/content/drive/MyDrive/TFG/audios/'+file[clip]+'.wav') 
  audio = '/content/drive/MyDrive/TFG/audios/'+file[clip]+'.wav'
  rate, data = wavfile.read(audio)

  #convert the audio from stereo to mono
  newaudiodata=stereoToMono(data)
  wavfile.write('/content/drive/MyDrive/TFG/audios/'+file[clip]+'_mono.wav', 44100, newaudiodata)
  mono = '/content/drive/MyDrive/TFG/audios/'+file[clip]+'_mono.wav'
  
  #remove background noise
  # load data
  rate, data = wavfile.read(mono)
  # perform noise reduction
  reduced_noise = nr.reduce_noise(y=data, sr=rate)
  wavfile.write('/content/drive/MyDrive/TFG/audios/'+file[clip]+'_new.wav', 44100, reduced_noise)

  #join video with audio
  audio = mp.AudioFileClip('/content/drive/MyDrive/TFG/audios/'+file[clip]+'_new.wav')
  video = mp.VideoFileClip('/content/drive/MyDrive/WhitneyWeikum_AVSpeech/'+file[clip]+'.avi')
  final = video.set_audio(audio)
  final.write_videofile('/content/drive/MyDrive/TFG/newVideos/'+file[clip]+'.mp4',codec= 'mpeg4' ,audio_codec='libvorbis')


  print('video'+ str(clip) +'done')


[MoviePy] Writing audio in /content/drive/MyDrive/TFG/audios/bi1-e01.wav


100%|██████████| 232/232 [00:00<00:00, 1576.97it/s]

[MoviePy] Done.


[MoviePy] >>>> Building video /content/drive/MyDrive/TFG/newVideos/bi1-e01.mp4
[MoviePy] Writing audio in bi1-e01TEMP_MPY_wvf_snd.ogg


100%|██████████| 232/232 [00:00<00:00, 924.93it/s]

...

[MoviePy] >>>> Building video /content/drive/MyDrive/TFG/newVideos/bi6-f37.mp4
[MoviePy] Writing audio in bi6-f37TEMP_MPY_wvf_snd.ogg


100%|██████████| 173/173 [00:00<00:00, 863.20it/s]

[MoviePy] Done.
[MoviePy] Writing video /content/drive/MyDrive/TFG/newVideos/bi6-f37.mp4



100%|██████████| 235/235 [00:01<00:00, 206.07it/s]


[MoviePy] Done.
[MoviePy] >>>> Video ready: /content/drive/MyDrive/TFG/newVideos/bi6-f37.mp4 

video169done


# SEPARATED PARTS

In [ ]:
#extract the audio from the video
my_clip = mp.VideoFileClip(r'/content/drive/MyDrive/WhitneyWeikum_AVSpeech/'+file+'.avi')
my_clip.audio.write_audiofile(r'/content/drive/MyDrive/TFG/audios/'+file+'.wav') 

[MoviePy] Writing audio in /content/drive/MyDrive/TFG/audios/bi1-e01.wav


100%|██████████| 232/232 [00:00<00:00, 1419.16it/s]

[MoviePy] Done.


In [ ]:
#listen to the audio with bakcground noise
audio = 'bi1-e01.wav'
IPython.display.Audio(data=audio, rate=44100)

In [ ]:
rate, data = wavfile.read(audio)

In [ ]:
#convert the audio from stereo to mono
newaudiodata=stereoToMono(data)
wavfile.write('/content/drive/MyDrive/TFG/audios/bi1-e01_mono.wav', 44100, newaudiodata)
mono = '/content/drive/MyDrive/TFG/audios/bi1-e01_mono.wav'

/content/drive/MyDrive/TFG/audios/bi1-e01_mono.wav


In [ ]:
#remove background noise
# load data
rate, data = wavfile.read(mono)
# perform noise reduction
reduced_noise = nr.reduce_noise(y=data, sr=rate)
wavfile.write('/content/drive/MyDrive/TFG/audios/bi1-e01_new.wav', 44100, reduced_noise)

In [ ]:
#listen to the new audio
IPython.display.Audio(data=reduced_noise, rate=44100)

In [ ]:
#join the new audio with the video

audio = mp.AudioFileClip('/content/drive/MyDrive/TFG/audios/bi1-e01_new.wav')
video = mp.VideoFileClip('/content/drive/MyDrive/WhitneyWeikum_AVSpeech/bi1-e01.avi')
final = video.set_audio(audio)
final.write_videofile("/content/drive/MyDrive/TFG/audios/bi1-e01.mp4",codec= 'mpeg4' ,audio_codec='libvorbis')


[MoviePy] >>>> Building video /content/drive/MyDrive/TFG/audios/bi1-e01.mp4
[MoviePy] Writing audio in bi1-e01TEMP_MPY_wvf_snd.ogg


100%|██████████| 232/232 [00:00<00:00, 839.17it/s]

[MoviePy] Done.
[MoviePy] Writing video /content/drive/MyDrive/TFG/audios/bi1-e01.mp4



100%|██████████| 315/315 [00:01<00:00, 196.97it/s]

[MoviePy] Done.
[MoviePy] >>>> Video ready: /content/drive/MyDrive/TFG/audios/bi1-e01.mp4 



Citation of library nosisereduce


In [ ]:
@software{tim_sainburg_2019_3243139,
  author       = {Tim Sainburg},
  title        = {timsainb/noisereduce: v1.0},
  month        = jun,
  year         = 2019,
  publisher    = {Zenodo},
  version      = {db94fe2},
  doi          = {10.5281/zenodo.3243139},
  url          = {https://doi.org/10.5281/zenodo.3243139}
}


@article{sainburg2020finding,
  title={Finding, visualizing, and quantifying latent structure across diverse animal vocal repertoires},
  author={Sainburg, Tim and Thielk, Marvin and Gentner, Timothy Q},
  journal={PLoS computational biology},
  volume={16},
  number={10},
  pages={e1008228},
  year={2020},
  publisher={Public Library of Science}
}

SyntaxError: ignored